# Model Refinement: Fine-Tuning Hyperparameters for Enhanced Performance

In [1]:
# Import necessary libraries
import numpy as np  
import optuna  # Hyperparameter optimization
import pandas as pd  
import xgboost as xgb  

from xgboost import XGBClassifier 
from sklearn.metrics import (
    accuracy_score, 
    precision_score, 
    recall_score, 
    f1_score, 
    roc_auc_score, 
    classification_report, 
    confusion_matrix, 
    make_scorer
)  # Evaluation metrics

from sklearn.model_selection import cross_val_score, train_test_split  # Model selection tools


/Users/spd/anaconda3/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# load training dataset
train_data = pd.read_csv("../data/training.csv")
# load test dataset
test_data = pd.read_csv("../data/Test.csv")
train_data.head()

ID Promotion  purchase  V1         V2        V3  V4  V5  V6  V7
0   1        No         0   2  30.443518 -1.165083   1   1   3   2
1   3        No         0   3  32.159350 -0.645617   2   3   2   2
2   4        No         0   2  30.431659  0.133583   1   1   4   2
3   5        No         0   0  26.588914 -0.212728   2   1   4   2
4   8       Yes         0   3  28.044331 -0.385883   1   1   2   2

In [3]:
# define Group A as g1, Group B as g2
g1 = train_data[(train_data.Promotion == "No")]
g2 = train_data[(train_data.Promotion == "Yes")]

In [4]:
# split the dataset into training and testing sets, only from group 2
X = g2[["V1", "V2", "V3", "V4", "V5", "V6", "V7"]]
y = g2["purchase"]
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)

In [5]:
# Promotion strategy function
def promotion_strategy(df, model):
    """
    Predicts purchases for the given DataFrame and converts predictions into "Yes" or "No" format for promotions.

    Args:
        df (pd.DataFrame): DataFrame containing columns V1 to V7.
        model: Trained model used for predictions.

    Returns:
        np.array: 1-D Numpy array with values 'Yes' or 'No' indicating whether an individual should receive a promotion.
    """
    arr = model.predict(df)  # Predict using the model

    # Replace predicted values: 1 -> "Yes", 0 -> "No"
    promotion = np.where(arr == 1, "Yes", "No")

    return promotion

# Score function to evaluate treatment effects
def score(df, promo_pred_col='Promotion'):
    n_treat = df.loc[df[promo_pred_col] == 'Yes', :].shape[0]  # Number of treated individuals
    n_control = df.loc[df[promo_pred_col] == 'No', :].shape[0]  # Number of control individuals
    n_treat_purch = df.loc[df[promo_pred_col] == 'Yes', 'purchase'].sum()  # Purchases in treatment group
    n_ctrl_purch = df.loc[df[promo_pred_col] == 'No', 'purchase'].sum()  # Purchases in control group

    # Calculate Incremental Response Rate (IRR)
    irr = n_treat_purch / n_treat - n_ctrl_purch / n_control
    # Calculate Net Incremental Revenue (NIR)
    nir = 10 * n_treat_purch - 0.15 * n_treat - 10 * n_ctrl_purch

    return (irr, nir)  

# Function to evaluate test results
def test_results(promotion_strategy, model):
    test_data = pd.read_csv('../data/Test.csv') 
    df = test_data[['V1', 'V2', 'V3', 'V4', 'V5', 'V6', 'V7']]  # Select relevant columns
    promos = promotion_strategy(df, model)  # Get promotion predictions
    score_df = test_data.iloc[np.where(promos == 'Yes')]  
    irr, nir = score(score_df)  # Calculate IRR and NIR for the filtered data

    return irr, nir  

In [6]:
# get metrics baseline
df = pd.read_csv('../reports/baselines/metric_baseline.csv')
df

scoring       score       irr  \
0                                           accuracy    0.947774  0.015825   
1                                            roc_auc    0.653748  0.020099   
2                                             recall    0.855563  0.014231   
3                                          precision    0.026520  0.019668   
4                                                 f1    0.050820  0.019597   
5  make_scorer(treat_score, response_method='pred...    0.025944  0.019763   
6  make_scorer(irr_score, response_method='predict')    0.017762  0.020606   
7  make_scorer(nir_score, response_method='predict')  132.760000  0.017863   
8  make_scorer(irr_nir_score, response_method='pr...    2.432661  0.018437   

      nir  n_promotions  n_trials  \
0   10.25          2116       500   
1  464.70         18739       500   
2 -107.90         28355       500   
3  394.45         17401       500   
4  416.55         18553       500   
5  415.75         17907       500   
6  519.65         19101       500   
7  321.70         23166       500   
8  394.30         23361       500   

                                         best_params  
0  {'max_depth': 7, 'learning_rate': 0.0977444529...  
1  {'max_depth': 4, 'learning_rate': 0.0100143392...  
2  {'max_depth': 1, 'learning_rate': 0.0229251660...  
3  {'max_depth': 3, 'learning_rate': 0.0325975613...  
4  {'max_depth': 3, 'learning_rate': 0.0295476606...  
5  {'max_depth': 3, 'learning_rate': 0.0193394409...  
6  {'max_depth': 3, 'learning_rate': 0.0183463400...  
7  {'max_depth': 1, 'learning_rate': 0.0736641572...  
8  {'max_depth': 1, 'learning_rate': 0.0463310264...

In [7]:
# Get the top 3 metrics based on Net Incremental Revenue (NIR)
top3_metrics = df.sort_values('nir', ascending=False)[:3] 
top3_metrics  

scoring     score       irr  \
6  make_scorer(irr_score, response_method='predict')  0.017762  0.020606   
1                                            roc_auc  0.653748  0.020099   
4                                                 f1  0.050820  0.019597   

      nir  n_promotions  n_trials  \
6  519.65         19101       500   
1  464.70         18739       500   
4  416.55         18553       500   

                                         best_params  
6  {'max_depth': 3, 'learning_rate': 0.0183463400...  
1  {'max_depth': 4, 'learning_rate': 0.0100143392...  
4  {'max_depth': 3, 'learning_rate': 0.0295476606...

In [8]:
for i in top3_metrics.best_params:
    print(i)

{'max_depth': 3, 'learning_rate': 0.018346340063285248, 'n_estimators': 190, 'gamma': 0.4018555699113115, 'subsample': 0.7127760681819945, 'colsample_bytree': 0.6612729951187046, 'reg_alpha': 0.4225060439585793, 'reg_lambda': 7.818764244426856, 'min_child_weight': 180}
{'max_depth': 4, 'learning_rate': 0.010014339210856402, 'n_estimators': 230, 'gamma': 0.9152647284098614, 'subsample': 0.9599231632005334, 'colsample_bytree': 0.5746419258296295, 'reg_alpha': 5.263941066575507, 'reg_lambda': 1.5566422117987755, 'min_child_weight': 232}
{'max_depth': 3, 'learning_rate': 0.029547660676442024, 'n_estimators': 190, 'gamma': 0.4651176483577494, 'subsample': 0.8040316521389101, 'colsample_bytree': 0.6671959012645239, 'reg_alpha': 6.363484166297619, 'reg_lambda': 1.205888741227787, 'min_child_weight': 275}


In [10]:
# Define the Optuna model tuning function
def objective(trial, scale_pos_weight, scoring):
    # Define hyperparameters for tuning based on insights from top 3 metrics
    params = {
        "verbosity": 0,  # Suppress output during model training
        "max_depth": trial.suggest_int("max_depth", 3, 4),  # Maximum depth of the trees
        "learning_rate": trial.suggest_float("learning_rate", .01, .03),  # Step size shrinkage
        "n_estimators": trial.suggest_int("n_estimators", 150, 250),  # Number of boosting rounds
        "gamma": trial.suggest_float("gamma", .4, 1),  # Minimum loss reduction for tree partitioning
        "subsample": trial.suggest_float("subsample", .7, 1),  # Proportion of samples for training
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 0.7),  # Proportion of features for each tree
        "reg_alpha": trial.suggest_float("reg_alpha", 0.4, 7),  # L1 regularization term
        "reg_lambda": trial.suggest_float("reg_lambda", 0.4, 8),  # L2 regularization term
        "min_child_weight": trial.suggest_int("min_child_weight", 150, 300)  # Minimum sum of instance weight for child
    }

    # Set scale_pos_weight to address class imbalance
    model = XGBClassifier(scale_pos_weight=scale_pos_weight, n_jobs=-1, random_state=42, **params)
    scores = cross_val_score(model, X_train, y_train, cv=5, scoring=scoring)  # Perform cross-validation

    return scores.mean()  # Return the mean score from cross-validation

In [11]:
# Define the model tuning function for testing various scoring methods
def model_tuning(scoring, n_trials=2):
    """
    Tunes the XGBoostClassifier using the specified scoring method and saves results to the results dictionary.

    Args:
        scoring (str or make_scorer object): The scoring method to evaluate model performance.
        n_trials (int, optional): Number of trials for tuning. Defaults to 2.
    """
    # Calculate scale_pos_weight to address class imbalance in the training dataset
    scale_pos_weight = len(y_train[y_train == 0]) / len(y_train[y_train == 1]) + 5

    # Initialize Optuna study for hyperparameter optimization
    study = optuna.create_study(direction="maximize")
    study.optimize(lambda trial: objective(trial, scale_pos_weight, scoring), n_trials=n_trials)

    # Extract the best parameters and score from the optimization
    best_params = study.best_params
    score = study.best_value

    # Train the tuned model using the best parameters
    tuned_xgb_clf = XGBClassifier(scale_pos_weight=scale_pos_weight, random_state=42, **best_params)
    tuned_xgb_clf.fit(X_train, y_train)

    # Prepare the test dataset and predict promotions
    df = test_data[["V1", "V2", "V3", "V4", "V5", "V6", "V7"]]
    promotions = promotion_strategy(df, tuned_xgb_clf)
    n_promotions = promotions[promotions == "Yes"].shape[0]  # Count the number of promotions

    # Evaluate the model using test_results function
    irr, nir = test_results(promotion_strategy, tuned_xgb_clf)

    # Save the results to the results dictionary
    results["scoring"].append(scoring)
    results["score"].append(score)
    results["irr"].append(irr)
    results["nir"].append(nir)
    results["n_promotions"].append(n_promotions)
    results["n_trials"].append(n_trials)
    results["best_params"].append(best_params)

In [12]:
# define treat score, see https://en.wikipedia.org/wiki/Confusion_matrix
def treat_score(y_true, y_pred):
    tn, fp, fn, tp = confusion_matrix(y_true, y_pred).ravel()
    return tp / (tp + fn + fp)

# define irr score
def irr_score(y_true, y_pred):
    tn, fp, fn, tp = confusion_matrix(y_true, y_pred).ravel()
    return tp / (tp + fp) - fn / (fn + tn)

# define nir score
def nir_score(y_true, y_pred):
    tn, fp, fn, tp = confusion_matrix(y_true, y_pred).ravel()
    return (10 * tp - .15 * (tp + fp)) - 10 * fn

# combine irr score and nir score together
def irr_nir_score(y_true, y_pred):
    irr = irr_score(y_true, y_pred)
    nir = nir_score(y_true, y_pred)
    return irr * nir

In [13]:
# define scoring methods
scorers = [
    #"accuracy",  # Standard accuracy score
    "roc_auc",   # Area Under the Receiver Operating Characteristic Curve
    #"recall",    # Recall score
    #"precision",  # Precision score
    "f1",        # F1 score (harmonic mean of precision and recall)
    #make_scorer(treat_score),  # Custom treat score
    make_scorer(irr_score),     # Custom Incremental Response Rate (IRR)
    #make_scorer(nir_score),     # Custom Net Incremental Revenue (NIR)
    #make_scorer(irr_nir_score), # Custom combined IRR and NIR score
]

# define results as a dict 
results = {
    "scoring": [],
    "score": [],
    "irr": [],
    "nir": [],
    "n_promotions": [],
    "n_trials": [],
    "best_params": []
}

# loop scoring methods
for scorer in scorers:
    model_tuning(scorer, n_trials=5000)

[I 2024-07-20 16:31:14,962] A new study created in memory with name: no-name-7624e98a-ad7e-428a-a48e-dd38297b3f4a
[I 2024-07-20 16:31:15,436] Trial 0 finished with value: 0.6485251602751931 and parameters: {'max_depth': 4, 'learning_rate': 0.012606912949413338, 'n_estimators': 198, 'gamma': 0.6469279668847514, 'subsample': 0.8871840580818269, 'colsample_bytree': 0.5548207880835494, 'reg_alpha': 2.8639016384345584, 'reg_lambda': 0.9804227579990505, 'min_child_weight': 202}. Best is trial 0 with value: 0.6485251602751931.
[I 2024-07-20 16:31:15,991] Trial 1 finished with value: 0.647266802770669 and parameters: {'max_depth': 4, 'learning_rate': 0.010124651568190148, 'n_estimators': 226, 'gamma': 0.458470918858486, 'subsample': 0.7837654386784764, 'colsample_bytree': 0.568878513176124, 'reg_alpha': 4.457485941574984, 'reg_lambda': 6.767131103822663, 'min_child_weight': 258}. Best is trial 0 with value: 0.6485251602751931.
[I 2024-07-20 16:31:16,439] Trial 2 finished with value: 0.65037074

[I 2024-07-20 16:31:26,125] Trial 20 finished with value: 0.6500098678483525 and parameters: {'max_depth': 3, 'learning_rate': 0.01351007357934037, 'n_estimators': 187, 'gamma': 0.5805565269466401, 'subsample': 0.9005710399382965, 'colsample_bytree': 0.571484906929362, 'reg_alpha': 3.8111846689118747, 'reg_lambda': 2.154028563730359, 'min_child_weight': 222}. Best is trial 15 with value: 0.6519544112281013.
[I 2024-07-20 16:31:26,655] Trial 21 finished with value: 0.6506204144434671 and parameters: {'max_depth': 3, 'learning_rate': 0.010641080774611903, 'n_estimators': 167, 'gamma': 0.41357349554364153, 'subsample': 0.9004100935594409, 'colsample_bytree': 0.5850918897420305, 'reg_alpha': 1.735109861426242, 'reg_lambda': 4.623506482315223, 'min_child_weight': 285}. Best is trial 15 with value: 0.6519544112281013.
[I 2024-07-20 16:31:27,090] Trial 22 finished with value: 0.6513500781177991 and parameters: {'max_depth': 3, 'learning_rate': 0.010156897317308353, 'n_estimators': 170, 'gamma

[I 2024-07-20 16:31:36,288] Trial 40 finished with value: 0.6484998203518202 and parameters: {'max_depth': 4, 'learning_rate': 0.012496156782729802, 'n_estimators': 191, 'gamma': 0.9894787657620701, 'subsample': 0.8339248876579508, 'colsample_bytree': 0.532466499591806, 'reg_alpha': 2.1003413863776723, 'reg_lambda': 0.9375962879311697, 'min_child_weight': 275}. Best is trial 15 with value: 0.6519544112281013.
[I 2024-07-20 16:31:36,667] Trial 41 finished with value: 0.6511737737458956 and parameters: {'max_depth': 3, 'learning_rate': 0.01114378661306189, 'n_estimators': 162, 'gamma': 0.4509243255438633, 'subsample': 0.9878561443362142, 'colsample_bytree': 0.5779043089744681, 'reg_alpha': 3.601046987432106, 'reg_lambda': 7.782893420192487, 'min_child_weight': 290}. Best is trial 15 with value: 0.6519544112281013.
[I 2024-07-20 16:31:37,130] Trial 42 finished with value: 0.6514733379153339 and parameters: {'max_depth': 3, 'learning_rate': 0.01120270461899673, 'n_estimators': 163, 'gamma'

[I 2024-07-20 16:31:45,300] Trial 60 finished with value: 0.6511840517174345 and parameters: {'max_depth': 3, 'learning_rate': 0.01692889474458737, 'n_estimators': 155, 'gamma': 0.4284100824567683, 'subsample': 0.8062710082806802, 'colsample_bytree': 0.6235915329164257, 'reg_alpha': 6.102718923081088, 'reg_lambda': 0.40501603942694936, 'min_child_weight': 284}. Best is trial 15 with value: 0.6519544112281013.
[I 2024-07-20 16:31:45,728] Trial 61 finished with value: 0.6518926473873683 and parameters: {'max_depth': 3, 'learning_rate': 0.010020806423045838, 'n_estimators': 170, 'gamma': 0.40066876013757247, 'subsample': 0.9330763576938038, 'colsample_bytree': 0.6065322719607161, 'reg_alpha': 6.779161278645994, 'reg_lambda': 7.459934382949541, 'min_child_weight': 269}. Best is trial 15 with value: 0.6519544112281013.
[I 2024-07-20 16:31:46,094] Trial 62 finished with value: 0.651459647386989 and parameters: {'max_depth': 3, 'learning_rate': 0.010018469467893048, 'n_estimators': 178, 'gamm

[I 2024-07-20 16:31:54,746] Trial 80 finished with value: 0.6525346739003862 and parameters: {'max_depth': 4, 'learning_rate': 0.012175595046523338, 'n_estimators': 181, 'gamma': 0.5216981097649138, 'subsample': 0.8502558193888401, 'colsample_bytree': 0.5829425869874606, 'reg_alpha': 6.86237816762862, 'reg_lambda': 7.537215731845045, 'min_child_weight': 237}. Best is trial 80 with value: 0.6525346739003862.
[I 2024-07-20 16:31:55,239] Trial 81 finished with value: 0.6517550000891366 and parameters: {'max_depth': 4, 'learning_rate': 0.012068914027860454, 'n_estimators': 179, 'gamma': 0.5111763196181457, 'subsample': 0.999734858569566, 'colsample_bytree': 0.5865040448605778, 'reg_alpha': 6.854244734327963, 'reg_lambda': 6.997092890851614, 'min_child_weight': 236}. Best is trial 80 with value: 0.6525346739003862.
[I 2024-07-20 16:31:55,756] Trial 82 finished with value: 0.6518725584631788 and parameters: {'max_depth': 4, 'learning_rate': 0.0120062895812671, 'n_estimators': 181, 'gamma': 0

...

[I 2024-07-20 18:51:29,045] Trial 4900 finished with value: 0.01666229763272496 and parameters: {'max_depth': 3, 'learning_rate': 0.016648349473726624, 'n_estimators': 206, 'gamma': 0.4641265085941856, 'subsample': 0.9314708878408422, 'colsample_bytree': 0.5399338585748023, 'reg_alpha': 1.4572100102149008, 'reg_lambda': 1.6393455316385592, 'min_child_weight': 206}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:51:29,584] Trial 4901 finished with value: 0.017215957574397794 and parameters: {'max_depth': 3, 'learning_rate': 0.01426124772918462, 'n_estimators': 169, 'gamma': 0.4645710769854827, 'subsample': 0.9375151928391773, 'colsample_bytree': 0.52048374038155, 'reg_alpha': 1.2512637246302492, 'reg_lambda': 1.3861491434214264, 'min_child_weight': 192}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:51:30,112] Trial 4902 finished with value: 0.017027416963654222 and parameters: {'max_depth': 3, 'learning_rate': 0.015436917703773853, 'n_estima

[I 2024-07-20 18:51:40,907] Trial 4920 finished with value: 0.016697906174570034 and parameters: {'max_depth': 3, 'learning_rate': 0.01472487664526515, 'n_estimators': 179, 'gamma': 0.8261062568523222, 'subsample': 0.9175756668011159, 'colsample_bytree': 0.5718243121329107, 'reg_alpha': 0.9703385762318782, 'reg_lambda': 1.1521248362499286, 'min_child_weight': 210}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:51:41,548] Trial 4921 finished with value: 0.016833272695089392 and parameters: {'max_depth': 3, 'learning_rate': 0.015657811749057244, 'n_estimators': 172, 'gamma': 0.6450882886325705, 'subsample': 0.9319754036560793, 'colsample_bytree': 0.6989317163652516, 'reg_alpha': 0.6728465056346056, 'reg_lambda': 1.5612160158863961, 'min_child_weight': 211}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:51:42,132] Trial 4922 finished with value: 0.017146573926886816 and parameters: {'max_depth': 3, 'learning_rate': 0.015186669668239458, 'n_est

[I 2024-07-20 18:51:53,330] Trial 4940 finished with value: 0.016885960213806495 and parameters: {'max_depth': 3, 'learning_rate': 0.01553953648393498, 'n_estimators': 229, 'gamma': 0.48526535453869113, 'subsample': 0.9330171359304557, 'colsample_bytree': 0.5278366751204054, 'reg_alpha': 1.2489424406328868, 'reg_lambda': 2.1713704514861076, 'min_child_weight': 214}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:51:53,969] Trial 4941 finished with value: 0.016815140896593632 and parameters: {'max_depth': 3, 'learning_rate': 0.016246533540311556, 'n_estimators': 177, 'gamma': 0.42775947917278484, 'subsample': 0.9278878223074482, 'colsample_bytree': 0.6257856703379792, 'reg_alpha': 1.0077548309436253, 'reg_lambda': 0.8716006633264254, 'min_child_weight': 205}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:51:54,573] Trial 4942 finished with value: 0.017033805667077965 and parameters: {'max_depth': 3, 'learning_rate': 0.024311853295146544, 'n_e

[I 2024-07-20 18:52:05,780] Trial 4960 finished with value: 0.017177619850015348 and parameters: {'max_depth': 3, 'learning_rate': 0.01551732940245588, 'n_estimators': 170, 'gamma': 0.44821507663712684, 'subsample': 0.9227940827157461, 'colsample_bytree': 0.5362632302768113, 'reg_alpha': 3.039002988176271, 'reg_lambda': 0.8256430340203946, 'min_child_weight': 208}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:52:06,312] Trial 4961 finished with value: 0.017445684875021926 and parameters: {'max_depth': 3, 'learning_rate': 0.015059568316851187, 'n_estimators': 174, 'gamma': 0.891204219677232, 'subsample': 0.9294172235347584, 'colsample_bytree': 0.5269226123133798, 'reg_alpha': 0.6843172190646919, 'reg_lambda': 1.7079766892346562, 'min_child_weight': 198}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:52:07,026] Trial 4962 finished with value: 0.017050792760925183 and parameters: {'max_depth': 3, 'learning_rate': 0.01590465338628625, 'n_estim

[I 2024-07-20 18:52:18,421] Trial 4980 finished with value: 0.01707995515650236 and parameters: {'max_depth': 3, 'learning_rate': 0.01915286241189322, 'n_estimators': 178, 'gamma': 0.44571977486566755, 'subsample': 0.9279007744196888, 'colsample_bytree': 0.5177166028529696, 'reg_alpha': 3.0353280353548224, 'reg_lambda': 1.8275315809938544, 'min_child_weight': 206}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:52:19,061] Trial 4981 finished with value: 0.017073811225896632 and parameters: {'max_depth': 3, 'learning_rate': 0.014429548538550604, 'n_estimators': 171, 'gamma': 0.4843623900329927, 'subsample': 0.9158042173481998, 'colsample_bytree': 0.5673091135938158, 'reg_alpha': 3.2238374151630502, 'reg_lambda': 2.0762529575950865, 'min_child_weight': 210}. Best is trial 846 with value: 0.017762647729104315.
[I 2024-07-20 18:52:19,741] Trial 4982 finished with value: 0.01733907844725871 and parameters: {'max_depth': 3, 'learning_rate': 0.015620630983445046, 'n_esti

In [14]:
# Convert results dictionary into a DataFrame for better visualization and analysis
results_df = pd.DataFrame(results)
results_df

scoring     score       irr  \
0                                            roc_auc  0.654770  0.019731   
1                                                 f1  0.051305  0.020381   
2  make_scorer(irr_score, response_method='predict')  0.017763  0.020216   

      nir  n_promotions  n_trials  \
0  451.25         19572      5000   
1  497.30         18977      5000   
2  460.70         18300      5000   

                                         best_params  
0  {'max_depth': 4, 'learning_rate': 0.0100036811...  
1  {'max_depth': 3, 'learning_rate': 0.0258060210...  
2  {'max_depth': 3, 'learning_rate': 0.0158947161...

In [15]:
# save model tuning results as a CSV file
results_df.to_csv('../reports/tuning_results/model_tuning.csv', index=False)

## Conclusion

As observed, the refinement process has led to improvements in our scoring metrics.**F1** scores saw significant enhancements, contributing to a notable increase in the **Net Incremental Response (NIR)**. However, it is important to note that the **IRR (Incremental Response Rate) and  ROC_AUC** score experienced a slight decline.

Taking these results into consideration, we have decided to proceed with our **metric_baseline** model. This model achieved a final **IRR score** with an **NIR** of approximately 520. Despite the minor decrease in the IRR metric, the overall improvements in ROC AUC and F1 scores, along with the substantial boost in NIR, indicate a more effective and profitable model.

This balanced approach ensures that we optimize our model’s performance while aligning closely with our business objectives.

